# Single Particle performance plots


   * [GEN Level plots](#Gen-level)
   * [All clusters without selection](#All-clusters-without-selection)
      * [2D clusters per layer](#2D-clusters-per-layer)
      * [2D cluster energy](#2D-cluster-energy)
      * [2D cluster: # of TriggerCells](#2D-cluster:-#-of-TriggerCells)
      * [# of 3D clusters](##-of-3D-clusters)
   * [Cluster matched to GEN particles](#Cluster-matched-to-GEN-particles)
      * [2D clusters per layer](#2D-clusters-per-layer)
      * [2D clusters: # of Trigger Cells](#2D-clusters:-#-of-Trigger-Cells)
      * [2D Cluster Energy](#2D-Cluster-Energy)
      * [3D clusters: # of 2D components](#3D-clusters:-#-of-2D-components)
      * [3D cluster energy](#3D-cluster-energy)
   * [Resolution studies](#Resolution-Studies)
      * [3D cluster: pt resolution](#3D-cluster:-Pt-resolution)
      * [2D position resolution](#Postion-resolution-of-2D-clusters)
   * [Trigger Tower performance](#Trigger-Tower-plots)
      * [Towers matched to GEN](#Towers-matched-to-GEN-particles)
      * [Resolution studies](#Trigger-Tower-resolution)



In [2]:
import sys
sys.path.insert(0, '..')
import ROOT
import root_numpy as rnp
import python.l1THistos as histos
import math
import uuid
import pandas as pd

ROOT.enableJSVis()
#ROOT.enableJSVis()

#from drawingTools import *

normalized_histos = list()
     

Welcome to JupyROOT 6.14/02


In [3]:
# %load ../drawingTools
import ROOT
import math
import uuid

# some useful globals, mainly to deal with ROOT idiosyncrasies
c_idx = 0
p_idx = 0
colors = range(1, 6)
stuff = []
f_idx = 0

ROOT.gStyle.SetOptTitle(False)
ROOT.gStyle.SetPadBottomMargin(0.13)
ROOT.gStyle.SetPadLeftMargin(0.13)
ROOT.gStyle.SetPadRightMargin(0.13)

# ROOT.gStyle.SetCanvasBorderMode(0)
# ROOT.gStyle.SetCanvasColor(0)


def getText(text, ndc_x, ndc_y):
    global stuff
    rtext = ROOT.TLatex(ndc_x, ndc_y, text)
    stuff.append(rtext)
    rtext.SetNDC(True)
    # rtext.SetTextFont(40)
    rtext.SetTextSize(0.03)
    return rtext

def getLegend(x1=0.7, y1=0.71, x2=0.95, y2=0.85):
    global stuff
    legend = ROOT.TLegend(x1, y1, x2, y2)
    stuff.append(legend)
    legend.SetFillColor(0)
    legend.SetFillStyle(0)
    legend.SetBorderSize(0)
    legend.SetTextSize(0.05)
    return legend

def newCanvas(name=None, title=None, height=600, width=800, xdiv=0, ydiv=0, form=4):
    global c_idx
    if name is None:
        name = 'c_{}'.format(uuid.uuid4().hex[:6])
        c_idx += 1
    if title is None:
        title = name
    # print name, title, width, height
    canvas = ROOT.TCanvas(name, title, width, height)
    if(xdiv*ydiv != 0):
        canvas.Divide(xdiv, ydiv)
    global stuff
    stuff.append(canvas)
    return canvas

def drawAndProfileX(plot2d, miny=None, maxy=None, do_profile=True, options='', text=None):
    global p_idx
    if miny and maxy:
        plot2d.GetYaxis().SetRangeUser(miny, maxy)
    c = newCanvas()
    c.SetGrid(1, 1)
    c.cd()
    plot2d.Draw(options)
    ROOT.gPad.SetGrid(1, 1)
    ROOT.gStyle.SetGridColor(15)

    if do_profile:
        profname = plot2d.GetName()+'_prof_'+str(p_idx)
        p_idx += 1
        firstbin = 1
        lastbin = -1
        prof = plot2d.ProfileX(profname, firstbin, lastbin, 's')
        prof.SetMarkerColor(2)
        prof.SetLineColor(2)
        prof.Draw('same')

    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw('same')

    c.Draw()


def draw(histograms,
         labels,
         options='',
         norm=False,
         logy=False,
         min_y=None,
         max_y=None,
         text=None,
         y_axis_label=None,
         x_axis_label=None,
         v_lines=None,
         h_lines=None,
         do_stats=False,
         do_profile=False,
         do_ratio=False):
    global colors
    global stuff
    global p_idx


    # 0 - determine kind and # of histos
    n_histos = len(histograms)
    if n_histos == 0:
        print '[draw]**ERROR: empy histo list'
        return

    histo_class = histograms[0].ClassName()

    # 1 - check argument consisntency
    if 'TH2' not in histo_class and do_profile:
        print '[draw]**ERROR: do_profile set for histo of class: {}'.format(histo_class)
        return

    # TH1 histograms are overlayed
    # TH2 histograms are drawn side by side in the same canvas
    overlay = True
    if n_histos > 1:
        if 'TH2' in histo_class or 'TH3' in histo_class:
            overlay = False

    # 2 - determine canvas properties
    xdiv = 0
    ydiv = 0
    c_width = 800
    c_height = 600
    # do_ratio = False

    if do_ratio:
        c_height = 800

    if not overlay:
        xdiv = 2
        c_width = 1000.
        ydiv = math.ceil(float(n_histos)/2)
        c_height = 500*ydiv
    canvas = newCanvas(name=None,
                       title=None,
                       height=int(c_height),
                       width=int(c_width),
                       xdiv=int(xdiv),
                       ydiv=int(ydiv))
    if overlay:
        canvas.SetRightMargin(0.30)

    canvas.cd()
    leg = getLegend()

    drawn_histos = []
    # drawn_histos = histograms
    for hidx, hist in enumerate(histograms):
        if 'TGraph' not in histo_class:
            hist.SetStats(do_stats)
        opt = options
        if overlay:
            hist.SetLineColor(colors[hidx])
            if hidx:
                opt = 'same,'+options
            else:
                if 'TGraph' in histo_class:
                    opt = options+'PA'
        else:
            canvas.cd(hidx+1)
        # print hidx, opt
        d_hist = hist
        if norm:
            d_hist = hist.DrawNormalized(opt, 1.)
        else:
            hist.Draw(opt)

        if do_profile:
            profname = d_hist.GetName()+'_prof_'+str(p_idx)
            p_idx += 1
            firstbin = 1
            lastbin = -1
            prof = d_hist.ProfileX(profname, firstbin, lastbin, 's')
            prof.SetMarkerColor(2)
            prof.SetLineColor(2)
            prof.Draw('same')

        if overlay:
            leg.AddEntry(hist, labels[hidx], 'l')
        else:
            if text:
                newtext = '{}: {}'.format(labels[hidx], text)
                rtext = getText(newtext, 0.15, 0.85)
                rtext.Draw('same')
        drawn_histos.append(d_hist)

    if do_ratio:
        h_ratio = ROOT.TRatioPlot(drawn_histos[0], drawn_histos[1])
        stuff.append(h_ratio)
        h_ratio.Draw()

        pad = canvas.cd(1)
        h_ratio.GetUpperPad().SetBottomMargin(0)
        h_ratio.GetUpperPad().SetRightMargin(0.3)
        if logy:
            h_ratio.GetUpperPad().SetLogy()
        pad.Update()
        pad = canvas.cd(2)
        h_ratio.GetLowerPad().SetTopMargin(0)
        h_ratio.GetLowerPad().SetRightMargin(0.3)
        pad.Update()
        # hratio.GetLowerRefGraph().GetYaxis().SetRangeUser(-6, 6)

    canvas.Update()

    # we now set the axis properties
    max_value = max_y
    min_value = min_y

    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in drawn_histos])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in drawn_histos])*1.2
    # print min_value, max_value

    for hist in drawn_histos:
        hist.GetYaxis().SetRangeUser(min_value, max_value)
        if y_axis_label:
            hist.GetYaxis().SetTitle(y_axis_label)
        if x_axis_label:
            hist.GetXaxis().SetTitle(x_axis_label)

    canvas.Draw()

    # we draw additional stuff if needed
    if overlay:
        canvas.cd()
        leg.Draw()
        if text:
            rtext = getText(text, 0.15, 0.85)
            rtext.Draw("same")

    pad_range = range(0, 1)
    if not overlay:
        pad_range = range(1, len(histograms)+1)

    for pad_id in pad_range:
        canvas.cd(pad_id)
        if v_lines:
            for v_line_x in v_lines:
                aline = ROOT.TLine(v_line_x, ROOT.gPad.GetUymin(), v_line_x,  ROOT.gPad.GetUymax())
                aline.SetLineStyle(2)
                aline.Draw("same")
                stuff.append(aline)
        if h_lines:
            for h_line_y in h_lines:
                aline = ROOT.TLine(ROOT.gPad.GetUxmin(), h_line_y, ROOT.gPad.GetUxmax(),  h_line_y)
                aline.SetLineStyle(2)
                aline.Draw("same")
                stuff.append(aline)
        if logy:
            if not do_ratio:
                ROOT.gPad.SetLogy()

        ROOT.gPad.Update()
    canvas.Update()
    canvas.Draw()

    return canvas


In [4]:
# %load samples.py
import ROOT
import pandas as pd
import python.selections as selections

version = 'v64t'

files = {}
file_keys = {}


class RootFile:
    def __init__(self, file_name):
        global file
        self.file_name = file_name
        if self.file_name not in files.keys():
            print 'get file: {}'.format(self.file_name)
            files[self.file_name] = ROOT.TFile(self.file_name)
        self._file = files[self.file_name]
        self._file_keys = None

    def cd(self):
        self._file.cd()

    def GetListOfKeys(self):
        global file_keys
        if self.file_name not in file_keys.keys():
            print 'get list'
            file_keys[self.file_name] = self._file.GetListOfKeys()
        self._file_keys = file_keys[self.file_name]
        return self._file_keys


class Sample():
    def __init__(self, name, label, version=None, type=None):
        self.name = name
        self.label = label
        if version:
            version = '_'+version
        else:
            version = ''
        self.histo_filename = '../plots1/histos_{}{}.root'.format(self.name, version)
        self.histo_file = ROOT.TFile(self.histo_filename, 'r')
        self.type = type


# sample_names = ['ele_flat2to100_PU0',
#                 'ele_flat2to100_PU200',
#                 'photonPt35_PU0',
#                 'photonPt35_PU200']


def get_label_dict(selections):
    dictionary = {}
    for sel in selections:
        dictionary[sel.name] = sel.label
    return dictionary


class HProxy:
    def __init__(self, classtype, tp, tp_sel, gen_sel, root_file):
        self.classtype = classtype
        self.tp = tp
        self.tp_sel = tp_sel
        self.gen_sel = gen_sel
        self.root_file = root_file
        self.instance = None

    def get(self):
        if self.instance is None:
            name = '{}_{}_{}'.format(self.tp, self.tp_sel, self.gen_sel)
            if self.gen_sel is None:
                name = '{}_{}'.format(self.tp, self.tp_sel)
            self.instance = self.classtype(name, self.root_file)
        return self.instance


class HPlot:
    def __init__(self, samples, tp_sets, tp_selections, gen_selections):
        self.tp_sets = tp_sets
        self.tp_selections = tp_selections
        self.gen_selections = gen_selections
        self.pus = []
        self.labels_dict = {}

        for sample in samples:
            self.pus.append(sample.label)
            self.labels_dict[sample.type] = sample.type

        self.data = pd.DataFrame(columns=['sample', 'pu', 'tp', 'tp_sel', 'gen_sel', 'classtype', 'histo'])

        self.labels_dict.update(tp_sets)
        self.labels_dict.update(tp_selections)
        self.labels_dict.update(gen_selections)
        self.labels_dict.update({'PU0': 'PU0', 'PU200': 'PU200'})

    def cache_histo(self,
                    classtype,
                    samples,
                    pus,
                    tps,
                    tp_sels,
                    gen_sels):
        if gen_sels is None:
            gen_sels = [None]

        for sample in samples:
            print sample
            for tp in tps:
                for tp_sel in tp_sels:
                    for gen_sel in gen_sels:
                        print sample, tp, tp_sel, gen_sel
                        self.data = self.data.append({'sample': sample.type,
                                                      'pu': sample.label,
                                                      'tp': tp,
                                                      'tp_sel': tp_sel,
                                                      'gen_sel': gen_sel,
                                                      'classtype': classtype,
                                                      'histo': HProxy(classtype, tp, tp_sel, gen_sel, sample.histo_file)},
                                                     ignore_index=True)

    def get_histo(self,
                  classtype,
                  sample=None,
                  pu=None,
                  tp=None,
                  tp_sel=None,
                  gen_sel=None):
        histo = None
        labels = []
        text = ''

        query = '(pu == @pu) & (tp == @tp) & (tp_sel == @tp_sel) & (classtype == @classtype)'
        if gen_sel is not None:
            query += ' & (gen_sel == @gen_sel)'
        else:
            query += ' & (gen_sel.isnull())'
        if sample is not None:
            query += '& (sample == @sample)'

        histo_df = self.data.query(query)

        if histo_df.empty:
            print 'No match found for: pu: {}, tp: {}, tp_sel: {}, gen_sel: {}, classtype: {}'.format(pu, tp, tp_sel, gen_sel, classtype)
            return None, None, None
#         print histo_df

        field_counts = histo_df.apply(lambda x: len(x.unique()))
        label_fields = []
        text_fields = []
        # print field_counts
        for field in field_counts.iteritems():
            if(field[1] > 1 and field[0] != 'histo'):
                label_fields.append(field[0])
            if(field[1] == 1 and field[0] != 'histo' and field[0] != 'classtype' and field[0] != 'sample'):
                if(gen_sel is None and field[0] == 'gen_sel'):
                    continue
                text_fields.append(field[0])
#         print 'label fields: {}'.format(label_fields)
#         print 'text fields: {}'.format(text_fields)

        for item in histo_df[label_fields].iterrows():
            labels.append(', '.join([self.labels_dict[tx] for tx in item[1].values if self.labels_dict[tx] != '']))

        # print labels
        text = ', '.join([self.labels_dict[fl] for fl in histo_df[text_fields].iloc[0].values if self.labels_dict[fl] != ''])
        histo = [his.get() for his in histo_df['histo'].values]
        return histo, labels, text


# -------------------------------------------------------------------------

samples_ele = [
    Sample('ele_flat2to100_PU0', 'PU0', version, 'ele'),
    Sample('ele_flat2to100_PU200', 'PU200', version, 'ele')
    ]

samples_photons = [
    Sample('photon_flat8to150_PU0', 'PU0', version, 'photon'),
    Sample('photon_flat8to150_PU200', 'PU200', version, 'photon')
    ]

samples_pions = [
    Sample('pion_flat2to100_PU0', 'PU0', version, 'pions'),
    ]

samples_nugus = [
    Sample('nugun_alleta_pu0', 'PU0', version, 'mb'),
    Sample('nugun_alleta_pu200', 'PU200', version, 'mb')
    ]

samples_nugunrates = [
    Sample('nugun_alleta_pu200', 'PU200', version, 'mb')
    ]

tpsets = {'DEF': 'NNDR',
          'DEFCalib': 'NNDR Calib v1'}

tpset_selections = {}
gen_selections = {}
samples = []

# tpset_selections.update(get_label_dict(tp_rate_selections))
tpset_selections.update(get_label_dict(selections.tp_match_selections))
gen_selections.update(get_label_dict(selections.gen_part_selections))
gen_selections.update({'nomatch': ''})


gen_part_selections: 10


Error in <TFile::TFile>: file ../plots1/histos_photon_flat8to150_PU0_v64t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_photon_flat8to150_PU200_v64t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_pion_flat2to100_PU0_v64t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_nugun_alleta_pu0_v64t.root does not exist


In [5]:
tpsets = {'L1Trk': 'L1Trk'}

tpset_selections = {}

gen_selections = {}
samples = []


#tpset_selections.update(get_label_dict(tp_rate_selections))
tpset_selections.update(get_label_dict(selections.tracks_selections))
gen_selections.update(get_label_dict(selections.gen_part_selections))
gen_selections.update({'nomatch': 'nomatch', 'GEN': 'GEN'})
samples = samples_ele



## Electron flat pT gun 2 < pt < 100 GeV

In [6]:
%%time

hplot = HPlot(samples, tpsets, tpset_selections, gen_selections)


hplot.cache_histo(classtype=histos.HistoSetEff, 
                  samples=samples,
                  pus=[],
                  tps=tpsets,
                  tp_sels=tpset_selections,
                  gen_sels=gen_selections)


hplot.cache_histo(classtype=histos.TrackHistos, 
                  samples=samples,
                  pus=[],
                  tps=tpsets,
                  tp_sels=tpset_selections,
                  gen_sels=gen_selections)


<__main__.Sample instance at 0x11de65d88>
<__main__.Sample instance at 0x11de65d88> L1Trk all GENPt40
<__main__.Sample instance at 0x11de65d88> L1Trk all GENEtaC
<__main__.Sample instance at 0x11de65d88> L1Trk all GENEtaB
<__main__.Sample instance at 0x11de65d88> L1Trk all GENEtaD
<__main__.Sample instance at 0x11de65d88> L1Trk all GENEtaBC
<__main__.Sample instance at 0x11de65d88> L1Trk all GENPt30
<__main__.Sample instance at 0x11de65d88> L1Trk all GENPt20
<__main__.Sample instance at 0x11de65d88> L1Trk all GENEtaBCD
<__main__.Sample instance at 0x11de65d88> L1Trk all GENPt10
<__main__.Sample instance at 0x11de65d88> L1Trk all nomatch
<__main__.Sample instance at 0x11de65d88> L1Trk all GEN
<__main__.Sample instance at 0x11de65d88> L1Trk Pt10 GENPt40
<__main__.Sample instance at 0x11de65d88> L1Trk Pt10 GENEtaC
<__main__.Sample instance at 0x11de65d88> L1Trk Pt10 GENEtaB
<__main__.Sample instance at 0x11de65d88> L1Trk Pt10 GENEtaD
<__main__.Sample instance at 0x11de65d88> L1Trk Pt10 GE

In [7]:
hplot.data

sample     pu     tp tp_sel    gen_sel                     classtype  \
0      ele    PU0  L1Trk    all    GENPt40  python.l1THistos.HistoSetEff   
1      ele    PU0  L1Trk    all    GENEtaC  python.l1THistos.HistoSetEff   
2      ele    PU0  L1Trk    all    GENEtaB  python.l1THistos.HistoSetEff   
3      ele    PU0  L1Trk    all    GENEtaD  python.l1THistos.HistoSetEff   
4      ele    PU0  L1Trk    all   GENEtaBC  python.l1THistos.HistoSetEff   
5      ele    PU0  L1Trk    all    GENPt30  python.l1THistos.HistoSetEff   
6      ele    PU0  L1Trk    all    GENPt20  python.l1THistos.HistoSetEff   
7      ele    PU0  L1Trk    all  GENEtaBCD  python.l1THistos.HistoSetEff   
8      ele    PU0  L1Trk    all    GENPt10  python.l1THistos.HistoSetEff   
9      ele    PU0  L1Trk    all    nomatch  python.l1THistos.HistoSetEff   
10     ele    PU0  L1Trk    all        GEN  python.l1THistos.HistoSetEff   
11     ele    PU0  L1Trk   Pt10    GENPt40  python.l1THistos.HistoSetEff   
12     ele    PU0  L1Trk   Pt10    GENEtaC  python.l1THistos.HistoSetEff   
13     ele    PU0  L1Trk   Pt10    GENEtaB  python.l1THistos.HistoSetEff   
14     ele    PU0  L1Trk   Pt10    GENEtaD  python.l1THistos.HistoSetEff   
15     ele    PU0  L1Trk   Pt10   GENEtaBC  python.l1THistos.HistoSetEff   
16     ele    PU0  L1Trk   Pt10    GENPt30  python.l1THistos.HistoSetEff   
17     ele    PU0  L1Trk   Pt10    GENPt20  python.l1THistos.HistoSetEff   
18     ele    PU0  L1Trk   Pt10  GENEtaBCD  python.l1THistos.HistoSetEff   
19     ele    PU0  L1Trk   Pt10    GENPt10  python.l1THistos.HistoSetEff   
20     ele    PU0  L1Trk   Pt10    nomatch  python.l1THistos.HistoSetEff   
21     ele    PU0  L1Trk   Pt10        GEN  python.l1THistos.HistoSetEff   
22     ele    PU0  L1Trk    Pt2    GENPt40  python.l1THistos.HistoSetEff   
23     ele    PU0  L1Trk    Pt2    GENEtaC  python.l1THistos.HistoSetEff   
24     ele    PU0  L1Trk    Pt2    GENEtaB  python.l1THistos.HistoSetEff   
25     ele    PU0  L1Trk    Pt2    GENEtaD  python.l1THistos.HistoSetEff   
26     ele    PU0  L1Trk    Pt2   GENEtaBC  python.l1THistos.HistoSetEff   
27     ele    PU0  L1Trk    Pt2    GENPt30  python.l1THistos.HistoSetEff   
28     ele    PU0  L1Trk    Pt2    GENPt20  python.l1THistos.HistoSetEff   
29     ele    PU0  L1Trk    Pt2  GENEtaBCD  python.l1THistos.HistoSetEff   
..     ...    ...    ...    ...        ...                           ...   
102    ele  PU200  L1Trk    all    GENEtaD  python.l1THistos.TrackHistos   
103    ele  PU200  L1Trk    all   GENEtaBC  python.l1THistos.TrackHistos   
104    ele  PU200  L1Trk    all    GENPt30  python.l1THistos.TrackHistos   
105    ele  PU200  L1Trk    all    GENPt20  python.l1THistos.TrackHistos   
106    ele  PU200  L1Trk    all  GENEtaBCD  python.l1THistos.TrackHistos   
107    ele  PU200  L1Trk    all    GENPt10  python.l1THistos.TrackHistos   
108    ele  PU200  L1Trk    all    nomatch  python.l1THistos.TrackHistos   
109    ele  PU200  L1Trk    all        GEN  python.l1THistos.TrackHistos   
110    ele  PU200  L1Trk   Pt10    GENPt40  python.l1THistos.TrackHistos   
111    ele  PU200  L1Trk   Pt10    GENEtaC  python.l1THistos.TrackHistos   
112    ele  PU200  L1Trk   Pt10    GENEtaB  python.l1THistos.TrackHistos   
113    ele  PU200  L1Trk   Pt10    GENEtaD  python.l1THistos.TrackHistos   
114    ele  PU200  L1Trk   Pt10   GENEtaBC  python.l1THistos.TrackHistos   
115    ele  PU200  L1Trk   Pt10    GENPt30  python.l1THistos.TrackHistos   
116    ele  PU200  L1Trk   Pt10    GENPt20  python.l1THistos.TrackHistos   
117    ele  PU200  L1Trk   Pt10  GENEtaBCD  python.l1THistos.TrackHistos   
118    ele  PU200  L1Trk   Pt10    GENPt10  python.l1THistos.TrackHistos   
119    ele  PU200  L1Trk   Pt10    nomatch  python.l1THistos.TrackHistos   
120    ele  PU200  L1Trk   Pt10        GEN  python.l1THistos.TrackHistos   
121    ele  PU200  L1Trk    Pt2    GENPt40  python.l1THistos.TrackHistos   
122    ele  PU200  L1Trk    Pt2    GENEtaC  python.l

In [8]:
tps = ['L1Trk']
tp_select = ['all', 'St']
gen_select = ['nomatch', 'GENEtaBC']


### Gen level particle distribution

In [10]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_den.h_pt for his in hsets], labels, norm=True, text=text, v_lines=[1.0])
            draw([his.h_den.h_eta for his in hsets], labels, norm=True, text=text, v_lines=[-2.8,-2.4,-1.7,-1.52,2.8,2.4,1.7,1.52])
            draw([his.h_den.h_fBrem for his in hsets], labels, norm=True, text=text)
            draw([his.h_den.h_reachedEE for his in hsets], labels, norm=True, text=text)
            


No match found for: pu: ['PU0', 'PU200'], tp: L1Trk, tp_sel: St, gen_sel: GEN, classtype: python.l1THistos.HistoSetEff


TypeError: 'NoneType' object is not iterable

#### 3D clusters matched to GEN

In [11]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_pt for his in hsets], labels, norm=True, text=text)
   

No match found for: pu: ['PU0', 'PU200'], tp: L1Trk, tp_sel: St, gen_sel: nomatch, classtype: python.l1THistos.TrackHistos


TypeError: 'NoneType' object is not iterable

In [12]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'nomatch']:
            print tp_sel, gen_sel
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_eta for his in hsets], labels, norm=True, text=text, options='hist')
  

all GEN
all nomatch
St GEN
No match found for: pu: ['PU0', 'PU200'], tp: L1Trk, tp_sel: St, gen_sel: GEN, classtype: python.l1THistos.TrackHistos


TypeError: 'NoneType' object is not iterable

In [31]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'GENEtaBC', 'nomatch']:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_pt for his in hsets], labels, norm=True, text=text)
  

In [32]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'GENEtaBC', 'nomatch']:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_chi2 for his in hsets], labels, norm=True, text=text)
  

In [33]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'GENEtaBC', 'nomatch']:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_nstubs for his in hsets], labels, norm=True, text=text)
  

In [34]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'GENEtaBC', 'nomatch']:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_z0 for his in hsets], labels, norm=True, text=text)
 

In [35]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'GENEtaBC', 'nomatch']:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_z0Veta for his in hsets], labels, text=text, options='COLZ')
 

In [36]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'GENEtaBC', 'nomatch']:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_chi2Veta for his in hsets], labels, text=text, options='COLZ')
 

In [37]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'GENEtaBC', 'nomatch']:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_nstubsVeta for his in hsets], labels, text=text, options='COLZ')
 

In [38]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN', 'GENEtaBC', 'nomatch']:
            hsets, labels, text = hplot.get_histo(histos.TrackHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            draw([his.h_nstubsVpt for his in hsets], labels, text=text, options='COLZ')
 

In [39]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN']:
            hsets, labels, text = hplot.get_histo(histos.EGHistos, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            drawSame([his.h_hwQual for his in hsets], labels, norm=True, text=text)
  

No match found for: pu: ['PU0', 'PU200'], tp: L1Trk, tp_sel: all, gen_sel: GEN, classtype: python.l1THistos.EGHistos


NameError: name 'drawSame' is not defined